## System Description
1. We have a set of COFs from a database. Each COF is characterized by a feature vector $$x_{COF} \in X \subset R^d$$ were d=14.


2. We have **two different types** of simulations to calculate **the same material property $S_{Xe/Kr}$**. Therefore, we have a Single-Task/Objective 
$$argmax_{x_{COF} \in X}[S_{Xe/Kr}(x_{COF})]$$

3. Multi-Fidelity problem. 
    1. low-fidelity  => Henry coefficient calculation - MC integration: $S_{Xe/Kr} = \frac{H_{Xe}}{H_{Kr}}$
    2. high-fidelity => GCMC mixture simulation - 80:20 (Kr:Xe) at 298 K and 1.0 bar: $S_{Xe/Kr} = \frac{n_{Xe} / n_{Kr}}{y_{Xe}/y_{Kr}}$


3. We will initialize the system with a few COFs at **both** fidelities in order to initialize the Covariance Matrix.
    1. The fist COF will be the one closest to the center of the normalized feature space
    2. The rest will be chosen to maximize diversity of the training set


4. Each surrogate model will **only train on data acquired at its level of fidelity** (Heterotopic data). $$X_{lf} \neq X_{hf} \subset X$$
    1. We  use the augmented-EI (aEI) acquisition function from [here](https://link.springer.com/content/pdf/10.1007/s00158-005-0587-0.pdf)
    2. Botorch GP surrogate model: [SingleTaskMultiFidelityGP](https://botorch.org/api/models.html#module-botorch.models.gp_regression_fidelity)
    3. Needed to use [this](https://botorch.org/api/optim.html#module-botorch.optim.fit) optimizer to correct matrix jitter
    4. Helpful [tutorial](https://botorch.org/tutorials/discrete_multi_fidelity_bo) for a similar BoTorch Model used

In [1]:
import torch
import gpytorch
from botorch.models import SingleTaskMultiFidelityGP
from botorch.models.transforms.outcome import Standardize
from gpytorch.mlls import ExactMarginalLogLikelihood
from botorch import fit_gpytorch_model
from botorch.optim.fit import fit_gpytorch_torch # fix Cholecky jitter error
from scipy.stats import norm
from sklearn.decomposition import PCA
import math 
import numpy as np
import matplotlib.pyplot as plt
import pickle
import h5py # for .jld2 files
import os
import time

# config plot settings
plt.rcParams["font.size"] = 16

## Load Data

In [2]:
# change to: "normalized" => "min_max" and "standardized" => "zscore"
normalization = "normalized" 

In [3]:
###
#  load data: targets and features
###
file = h5py.File("targets_and_{}_features.jld2".format(normalization), "r")


# feature matrix
X = torch.from_numpy(np.transpose(file["X"][:]))
# simulation data
y = [torch.from_numpy(np.transpose(file["henry_y"][:])), 
     torch.from_numpy(np.transpose(file["gcmc_y"][:]))]
# associated simulation costs
cost = [np.transpose(file["henry_total_elapsed_time"][:]), 
        np.transpose(file["gcmc_elapsed_time"][:])]

# total number of COFs in data set
nb_COFs = X.shape[0] 


###
#  load data: initializing COFs
###
init_cof_ids_file = pickle.load(open(
                    'search_results/{}/initializing_cof_ids_{}.pkl'.format(normalization, normalization), 
                    'rb'))

init_cof_ids = init_cof_ids_file['init_cof_ids']

# total number of BO searches to run = number of initializing sets
nb_runs = len(init_cof_ids)


###
#  print information about data
###
# cost
print("total high-fidelity cost:", sum(cost[1]).item(), "[min]")
print("total low-fidelity cost: ", sum(cost[0]).item(), "[min]")
print("average high-fidelity cost:", np.mean(cost[1]), "[min]")
print("average low-fidelity cost: ", np.mean(cost[0]), "[min]")
print("average cost ratio:\t   ", np.mean(cost[1] / cost[0]))
# data shape
print("\nraw data - \n\tX:", X.shape)
for f in range(2):
    print("\tfidelity:", f)
    print("\t\ty:", y[f].shape)
    print("\t\tcost: ", cost[f].shape)
# normalization
print("\nEnsure features are normalized - ")
print("max:\n", torch.max(X, 0).values)
print("min:\n", torch.min(X, 0).values)
print("width:\n",torch.max(X, 0).values - torch.min(X, 0).values)
print("mean:\n", torch.mean(X, 0))
print("std:\n", torch.std(X, 0))

total high-fidelity cost: 139887.66223703226 [min]
total low-fidelity cost:  10076.305239888028 [min]
average high-fidelity cost: 230.0783918372241 [min]
average low-fidelity cost:  16.57287046034216 [min]
average cost ratio:	    13.444745568580501

raw data - 
	X: torch.Size([608, 14])
	fidelity: 0
		y: torch.Size([608])
		cost:  (608,)
	fidelity: 1
		y: torch.Size([608])
		cost:  (608,)

Ensure features are normalized - 
max:
 tensor([1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       dtype=torch.float64)
min:
 tensor([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
       dtype=torch.float64)
width:
 tensor([1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       dtype=torch.float64)
mean:
 tensor([0.2856, 0.5864, 0.5304, 0.3323, 0.0421, 0.1617, 0.6405, 0.6793, 0.0062,
        0.1758, 0.0308, 0.0131, 0.0132, 0.0238], dtype=torch.float64)
std:
 tensor([0.1586, 0.1787, 0.1896, 0.1512, 0.1150, 0.1916, 0.1631, 0.1354, 0.0631,
        0.1126, 0.1026, 0.0935,

# TODO:

### from botorch.models.transforms.input import Normalize
### X_tf = X.Normalize()


okay, so I think that the immediate plan is going to have to be to generate a file of the raw feature vectors
and pass those into the model while using the `input_transform=Normalize(d=?)` or the `input_transform=Standardize(d=?)` where `d = the dimension of the input space`. 

- [normalization](https://botorch.org/api/_modules/botorch/models/transforms/input.html#Normalize)
- [standardization](https://botorch.org/api/_modules/botorch/models/transforms/input.html#InputStandardize)


I will have to be sure to save the output of these models in files deparate from those of the BO runs that I have already made. This way I can avoid any issues with overwriting the data and wasting time.

Be certain that everything that gets done here happens for the SFBO!

**NOTE:**
Also, leave notes and links to papers and documentation wherever I can to help Cory in the writing process. This will also help the reader when going through the notebooks/project. For example, the optimizer used by the GP as well as which kernel function it is using.

Oh, and push a link (i.e. download a copy of the file as a ptx) to the MFBO_Fig1 powerpoint so Cory has access to it as well.

## Helper Functions

#### Post-Search Analysis

In [4]:
def calc_fidelity_fraction(acquired_set):
    nb_iters = len(acquired_set)
    fid_frac = np.zeros(nb_iters)
    for i in range(1, nb_iters):
        fid_frac[i] = sum(acquired_set[:, 0][:i+1]) / (i+1)
    return fid_frac

In [5]:
def get_y_maxes_acquired(acquired_set):    
    nb_iters = len(acquired_set)
    y_maxes = np.zeros(nb_iters)
    # we want the maximum y value (only high-fidelity) up to a given iteration
    y_max = 0.0 # update this each iteration.
    for i, (f_id, cof_id) in enumerate(acquired_set):
        y_acq_this_iter = y[f_id][cof_id]
        # i is iteration index
        if f_id == 1 and y_acq_this_iter > y_max:
            y_max = y_acq_this_iter # over-write max
        y_maxes[i] = y_max 
    return y_maxes

In [6]:
def accumulated_cost(cost_acquired):
    nb_iters = len(acquired_set)
    accumulated_cost = np.zeros(nb_iters)
    accumulated_cost[0] = cost_acquired[0]
    for i in range(1, len(cost_acquired)):
        accumulated_cost[i] = accumulated_cost[i-1] + cost_acquired[i]
    return accumulated_cost

#### Construct Initial Inputs

In [7]:
def initialize_acquired_set(X, y, initializing_COFs, discrete_fidelities):
#     cof_ids = diverse_set(X, nb_COFs_initialization) # np.array(ids_train)
    return torch.tensor([[f_id, cof_id] for cof_id in initializing_COFs for f_id in discrete_fidelities])

In [8]:
# construct feature matrix of acquired points
def build_X_train(acquired_set):
    cof_ids = [a[1] for a in acquired_set]
    f_ids = torch.tensor([a[0] for a in acquired_set])
    return torch.cat((X[cof_ids, :], f_ids.unsqueeze(dim=-1)), dim=1)

# construct output vector for acquired points
def build_y_train(acquired_set):
    return torch.tensor([y[f_id][cof_id] for f_id, cof_id in acquired_set]).unsqueeze(-1)

# construct vector to track accumulated cost of acquired points
def build_cost(acquired_set):
    return torch.tensor([cost[f_id][cof_id] for f_id, cof_id in acquired_set]).unsqueeze(-1)

# construct vector to track accumulated cost of acquired points
def build_cost_fidelity(acquired_set, fidelity):
    return torch.tensor([cost[f_id][cof_id] for f_id, cof_id in acquired_set if f_id == fidelity]).unsqueeze(-1)

#### test

In [9]:
def test_initializing_functions(X, y):
    ###
    #  construct training sets
    ###
    # list of (cof_id, fid_id)'s
    acquired_set = [[1, 10], [0, 3], [0, 4]]
    
    # Training Sets
    X_train = build_X_train(acquired_set)
    y_train = build_y_train(acquired_set)
    
    ###
    #  test that the constructor functions are working properly
    ###
    assert np.allclose(X[10, :], X_train[0, :14])
    assert X_train[0, 14] == 1
    assert X_train[1, 14] == 0
    assert y_train[0] == y[1][10] # y[fid_id][cof_id]
    assert y_train[2] == y[0][4]
    return

test_initializing_functions(X, y)

### Surrogate Model

In [10]:
def train_surrogate_model(X_train, y_train):
    model = SingleTaskMultiFidelityGP(
        X_train, 
        y_train, 
        outcome_transform=Standardize(m=1), # m is the output dimension
        data_fidelity=X_train.shape[1] - 1
    )   
    mll = ExactMarginalLogLikelihood(model.likelihood, model)
    fit_gpytorch_model(mll, optimizer=fit_gpytorch_torch)
    return model

### Acquisition Function

In [11]:
# calculate posterior mean and variance for a given fidelity
def mu_sigma(model, X, fidelity):
    f = torch.tensor((), dtype=torch.float64).new_ones((nb_COFs, 1)) * fidelity
    X_f = torch.cat((X, f), dim=1) # last col is associated fidelity
    f_posterior = model.posterior(X_f)
    return f_posterior.mean.squeeze().detach().numpy(), np.sqrt(f_posterior.variance.squeeze().detach().numpy())

# get the current best y-value of desired_fidelity in the acquired set
def get_y_max(acquired_set, desired_fidelity):
    return np.max([y[f_id][cof_id] for f_id, cof_id in acquired_set if f_id == desired_fidelity])

In [12]:
###
#  efficient multi-fidelity correlation function
#  corr(y at given fidelity, y at high-fidelity)
#  (see notes)
###
def mfbo_correlation_function(model, X, fidelity):
    # given fidelity
    f   = torch.tensor((), dtype=torch.float64).new_ones((nb_COFs, 1)) * fidelity
    X_f = torch.cat((X, f), dim=1) # last col is associated fidelity
    
    #  high-fidelity
    hf   = torch.tensor((), dtype=torch.float64).new_ones((nb_COFs, 1)) 
    X_hf = torch.cat((X, hf), dim=1) # last col is associated fidelity

    # combine into a single tensor
    X_all_fid = torch.cat((X_f, X_hf), dim=0)
    
    # get variance for each fidelity
    var_f = torch.flatten(model.posterior(X_f).variance)
    var_hf = torch.flatten(model.posterior(X_hf).variance) # variance
    
    # posterior covariance 
    cov = torch.diag(model(X_all_fid).covariance_matrix[:X_f.size()[0], X_f.size()[0]:])
    
    corr = cov / (torch.sqrt(var_f) * torch.sqrt(var_hf))
    return corr

In [13]:
###
#  cost ratio
###
def estimate_cost_ratio(fidelity, acquired_set):
    avg_cost_f  = torch.mean(build_cost_fidelity(acquired_set, fidelity))
    avg_cost_hf = torch.mean(build_cost_fidelity(acquired_set, 1))
    cr = avg_cost_hf / avg_cost_f
    return cr.item()

###
#  expected imrovement function, only uses hf
###
def EI_hf(model, X, acquired_set):
    hf_mu, hf_sigma = mu_sigma(model, X, 1)
    y_max = get_y_max(acquired_set, 1)
    
    z = (hf_mu - y_max) / hf_sigma
    explore_term = hf_sigma * norm.pdf(z) 
    exploit_term = (hf_mu - y_max) * norm.cdf(z) 
    ei = explore_term + exploit_term
    return np.maximum(ei, np.zeros(nb_COFs))

###
#  acquisition function
###
def acquisition_scores(model, X, fidelity, acquired_set):
    # expected improvement for high-fidelity
    ei = EI_hf(model, X, acquired_set) 
    
    # augmenting functions
    corr_f1_f0 = mfbo_correlation_function(model, X, fidelity)
    
    cr = estimate_cost_ratio(fidelity, acquired_set)

    scores = torch.from_numpy(ei) * corr_f1_f0 * cr
    return scores.detach().numpy()

def in_acquired_set(f_id, cof_id, acquired_set):
    for this_f_id, this_cof_id in acquired_set:
        if this_cof_id == cof_id and this_f_id == f_id:
            return True
    return False

### Bayesian Algorithm

In [14]:
def run_Bayesian_optimization(nb_iterations, initializing_COFs, verbose=False):
    assert nb_iterations > len(initializing_COFs)
    ###
    #  initialize system
    ###
    acquired_set = initialize_acquired_set(X, y, initializing_COFs, discrete_fidelities)
    
    ###
    #  itterate through remaining budget using BO
    ###
    for i in range(nb_COFs_initialization * len(discrete_fidelities), nb_iterations): 
        print("BO iteration: ", i)
        ###
        #  construct training data (perform experiments)
        ###
        X_train = build_X_train(acquired_set)
        y_train = build_y_train(acquired_set)

        if verbose:
            print("Initialization - \n")
            print("\tid acquired = ", [acq_[0].item() for acq_ in acquired_set])
            print("\tfidelity acquired = ", [acq_[1].item() for acq_ in acquired_set])
            print("\tcosts acquired = ", build_cost(acquired_set), " [min]")

            print("\n\tTraining data:\n")
            print("\t\t X train shape = ", X_train.shape)
            print("\t\t y train shape = ", y_train.shape)
            print("\t\t training feature vector = \n", X_train)
        
        ###
        #  train Model
        ###
        model = train_surrogate_model(X_train, y_train)

        ###
        #  acquire new (COF, fidelity) not yet acquired.
        ###
        # entry (fid_id, cof_id) is the acquisition value for fidelity f_id and cof cof_id
        the_acquisition_scores = np.array([acquisition_scores(model, X, f_id, acquired_set) for f_id in discrete_fidelities])
        # overwrite acquired COFs/fidelities with negative infinity to not choose these.
        for f_id, cof_id in acquired_set:
            the_acquisition_scores[f_id, cof_id] = - np.inf
        # select COF/fidelity with highest aquisition score.
        f_id, cof_id = np.unravel_index(np.argmax(the_acquisition_scores), np.shape(the_acquisition_scores))
        assert not in_acquired_set(f_id, cof_id, acquired_set)
        # update acquired_set
        acq = torch.tensor([[f_id, cof_id]], dtype=int)
        acquired_set = torch.cat((acquired_set, acq))

        ###
        #  print useful info
        ###
        if verbose:
            print("\tacquired COF ", cof_id, " at fidelity, ", f_id)
            print("\t\ty = ", y[f_id][cof_id].item())
            print("\t\tcost = ", cost[f_id][cof_id])
        
    return acquired_set

# Run MFBO

In [15]:
###
#  construct initial inputs
###
discrete_fidelities = [0, 1] # set of discrete fidelities to select from
nb_COFs_initialization = 3   # at each fidelity, number of COFs to initialize with
nb_iterations = 150          # BO budget, includes initializing COFs

In [16]:
###
#  run search
###
for j, initializing_COFs in enumerate(init_cof_ids): 
    # check the length of each initializing set
    assert len(initializing_COFs) == nb_COFs_initialization
    print("run #: {}".format(j))
    
    # start timer for BO run
    start_time = time.time()
    ###
    #  run BO search
    ###
    acquired_set = run_Bayesian_optimization(nb_iterations, initializing_COFs)
    
    ###
    #  post-run analysis
    ###
    elapsed_time  = time.time() - start_time
    print("elapsed_time:\t", elapsed_time / 60, " min.")
    y_acquired    = build_y_train(acquired_set)
    y_maxes_acq   = get_y_maxes_acquired(acquired_set.detach().numpy())
    fid_fraction  = calc_fidelity_fraction(acquired_set.detach().numpy())
    cost_acquired = build_cost(acquired_set)
    acc_cost      = accumulated_cost(cost_acquired.flatten().detach().numpy())
    
    ###
    # look at unique COFs acquired
    ###
    # cof_ids_acquired = torch.tensor([acq[1] for acq in acquired_set])
    n_unique_cofs_acquired = len(np.unique([acq[1] for acq in acquired_set]))
    print("total number of unique COFs acquired", n_unique_cofs_acquired)

    ###
    #  Iterations until top COF and accumulated 
    ###
    cof_id_with_max_selectivity = np.argmax(y[1])
    BO_iter_top_cof_acquired = float("inf") # dummy 
    for i, (f_id, cof_id) in enumerate(acquired_set):
        if cof_id == cof_id_with_max_selectivity and f_id == 1:
            BO_iter_top_cof_acquired = i
            print("woo, top COF acquired!")
            print("iteration we acquire top COF = ", BO_iter_top_cof_acquired) 
            break
        elif i == len(acquired_set)-1:
            print("oh no, top COF not acquired!")


    top_cof_acc_cost = sum(build_cost(acquired_set)[:BO_iter_top_cof_acquired])
    print("accumulated cost up to observation of top COF = ", top_cof_acc_cost.item(), " [min]")
    
    ###
    #  store results
    ###
    mfbo_res = dict({'acquired_set': acquired_set.detach().numpy(),
                     'y_acquired': y_acquired.detach().numpy(),
                     'y_max_acquired': y_maxes_acq,
                     'fidelity_fraction': fid_fraction,
                     'cost_acquired': cost_acquired.flatten().detach().numpy(),
                     'accumulated_cost': acc_cost / 60,
                     'nb_COFs_initialization': nb_COFs_initialization,
                     'BO_iter_top_cof_acquired': BO_iter_top_cof_acquired,
                     'elapsed_time (min)':  elapsed_time / 60
                    })

    with open('search_results/{}/mfbo_results/mfbo_results_run_{}.pkl'.format(normalization, j), 'wb') as file:
        pickle.dump(mfbo_res, file)

run #: 0
BO iteration:  6
Iter 10/100: 8.649966451577285
Iter 20/100: 6.26206755970746
Iter 30/100: 4.9909465606677434
Iter 40/100: 4.18377881356157
Iter 50/100: 3.9690264115947524
Iter 60/100: 3.8593285725557678
Iter 70/100: 3.814466705392395
Iter 80/100: 3.792974167909424
Iter 90/100: 3.783151879426909
Iter 100/100: 3.7761276175238065
BO iteration:  7
Iter 10/100: 7.632250650920198
Iter 20/100: 5.572069981168265
Iter 30/100: 4.456094986634148
Iter 40/100: 3.7145561522884245
Iter 50/100: 3.5556454359205065
Iter 60/100: 3.470555955829871
Iter 70/100: 3.4310039381264614
Iter 80/100: 3.411292441021827
Iter 90/100: 3.3999351933715007
Iter 100/100: 3.3904232290142886
BO iteration:  8
Iter 10/100: 6.865587544981905
Iter 20/100: 5.048079508976835
Iter 30/100: 4.053556062111394
Iter 40/100: 3.3948212169996066
Iter 50/100: 3.256478428924538
Iter 60/100: 3.1839070521364006
Iter 70/100: 3.149884353225813
Iter 80/100: 3.1318081591753666
Iter 90/100: 3.12087039121823
Iter 100/100: 3.11122745505999

Iter 70/100: 1.6166373904455669
Iter 80/100: 1.6110234231807463
Iter 90/100: 1.609289650390877
Iter 100/100: 1.6085835206074548
BO iteration:  35
Iter 10/100: 2.7459120552871163
Iter 20/100: 2.2495388398159792
Iter 30/100: 1.9553973665286635
Iter 40/100: 1.7581737779911362
Iter 50/100: 1.6414194137665477
Iter 60/100: 1.6183027825922538
Iter 70/100: 1.6001712087817315
Iter 80/100: 1.5947553044041565
Iter 90/100: 1.5929448161186497
Iter 100/100: 1.592273362015856
BO iteration:  36
Iter 10/100: 2.7090660862032254
Iter 20/100: 2.2225159593540287
Iter 30/100: 1.9307742176682499
Iter 40/100: 1.7374937262417909
Iter 50/100: 1.6222237990951578
Iter 60/100: 1.5993937258521984
Iter 70/100: 1.5814490576525622
Iter 80/100: 1.576040954512128
Iter 90/100: 1.5741822884167818
Iter 100/100: 1.5734333434062775
BO iteration:  37
Iter 10/100: 2.6739500286360807
Iter 20/100: 2.196673869536121
Iter 30/100: 1.9073206031181893
Iter 40/100: 1.7174368088343857
Iter 50/100: 1.603965073771527
Iter 60/100: 1.58079

BO iteration:  59
Iter 10/100: 2.210861544735932
Iter 20/100: 1.8618528336556694
Iter 30/100: 1.6107568903606932
Iter 40/100: 1.4168018793429002
Iter 50/100: 1.3598484171185572
Iter 60/100: 1.3182723325167065
Iter 70/100: 1.3093209139248412
Iter 80/100: 1.3044754381631838
Iter 90/100: 1.3023353706734295
Iter 100/100: 1.3017985033968587
BO iteration:  60
Iter 10/100: 2.1978385699771694
Iter 20/100: 1.8524026000892548
Iter 30/100: 1.6022907325675828
Iter 40/100: 1.407814760975793
Iter 50/100: 1.3522176885954778
Iter 60/100: 1.3104084439312982
Iter 70/100: 1.3014350255576943
Iter 80/100: 1.2965797779972292
Iter 90/100: 1.294441162985912
Iter 100/100: 1.2938662386675823
BO iteration:  61
Iter 10/100: 2.1841134031481135
Iter 20/100: 1.8418612069147822
Iter 30/100: 1.591817242472893
Iter 40/100: 1.3959557183060658
Iter 50/100: 1.34242594203859
Iter 60/100: 1.3005207212916314
Iter 70/100: 1.291550549199862
Iter 80/100: 1.2863061250739092
Iter 90/100: 1.2840054004563146
Iter 100/100: 1.2832938

Iter 70/100: 1.0849659315147346
Iter 80/100: 1.0809612146951946
Iter 90/100: 1.0801219654994765
Iter 100/100: 1.0798137555929188
BO iteration:  85
Iter 10/100: 1.9619168817092276
Iter 20/100: 1.6751500826170274
Iter 30/100: 1.4347982551471914
Iter 40/100: 1.2024303186069678
Iter 50/100: 1.1033707725944686
Iter 60/100: 1.0882062070480385
Iter 70/100: 1.0821578912166592
Iter 80/100: 1.0779312460977144
Iter 90/100: 1.0772145911647566
Iter 100/100: 1.0768353593708702
BO iteration:  86
Iter 10/100: 1.9555442568031807
Iter 20/100: 1.6707055025359963
Iter 30/100: 1.4311638093645012
Iter 40/100: 1.198376617437739
Iter 50/100: 1.1001088352393733
Iter 60/100: 1.0854043527594175
Iter 70/100: 1.0791040923653716
Iter 80/100: 1.075130814235446
Iter 90/100: 1.0739639143631508
Iter 100/100: 1.073515561661012
BO iteration:  87
Iter 10/100: 1.949551931884982
Iter 20/100: 1.6665466936176736
Iter 30/100: 1.4277797594571446
Iter 40/100: 1.1969140930918016
Iter 50/100: 1.0989424047384684
Iter 60/100: 1.0842

Iter 70/100: 1.094660700161547
Iter 80/100: 1.0912125113186542
Iter 90/100: 1.090580011330174
Iter 100/100: 1.090199450742097
BO iteration:  116
Iter 10/100: 1.803362419391325
Iter 20/100: 1.5579283461279687
Iter 30/100: 1.3304218700012624
Iter 40/100: 1.1672352491804037
Iter 50/100: 1.1086864686176194
Iter 60/100: 1.0920691484658023
Iter 70/100: 1.0840448129692595
Iter 80/100: 1.080662164697901
Iter 90/100: 1.0799455236958644
Iter 100/100: 1.079605314109386
BO iteration:  117
Iter 10/100: 1.796955431819004
Iter 20/100: 1.5506460945295302
Iter 30/100: 1.3190765764771544
Iter 40/100: 1.1503133049951273
Iter 50/100: 1.0953402027362091
Iter 60/100: 1.0749266851607062
Iter 70/100: 1.0649491029407314
Iter 80/100: 1.0609296377614843
Iter 90/100: 1.059943522176859
Iter 100/100: 1.059443926573719
BO iteration:  118
Iter 10/100: 1.7927826103005504
Iter 20/100: 1.5471146984976156
Iter 30/100: 1.314421758721318
Iter 40/100: 1.140215456912684
Iter 50/100: 1.0890332402196237
Iter 60/100: 1.06590165

...

BO iteration:  46
Iter 10/100: 2.4148175644399963
Iter 20/100: 2.010512446968461
Iter 30/100: 1.7481570159652366
Iter 40/100: 1.591601066309363
Iter 50/100: 1.4266985757759982
Iter 60/100: 1.296249320000501
Iter 70/100: 1.2681043474847369
Iter 80/100: 1.2554147495372
Iter 90/100: 1.2503361699872588
Iter 100/100: 1.2495203018720227
BO iteration:  47
Iter 10/100: 2.3979906986318453
Iter 20/100: 2.002541668838452
Iter 30/100: 1.7458328532609442
Iter 40/100: 1.587320231201643
Iter 50/100: 1.428773254769443
Iter 60/100: 1.3045482007888438
Iter 70/100: 1.2774953386272876
Iter 80/100: 1.2648617163583582
Iter 90/100: 1.2600143943591535
Iter 100/100: 1.259262603308005
BO iteration:  48
Iter 10/100: 2.37898546721228
Iter 20/100: 1.990482359319227
Iter 30/100: 1.7375335184924843
Iter 40/100: 1.5803292059208207
Iter 50/100: 1.4311596875486545
Iter 60/100: 1.2842135181504515
Iter 70/100: 1.2643282548096757
Iter 80/100: 1.2586498743028376
Iter 90/100: 1.255997404001941
Iter 100/100: 1.25506317375519

Iter 100/100: 1.1523417800430271
BO iteration:  71
Iter 10/100: 2.0646007908561264
Iter 20/100: 1.7535107286151734
Iter 30/100: 1.5180811756199308
Iter 40/100: 1.3789882213507014
Iter 50/100: 1.287821577317661
Iter 60/100: 1.1685373081591746
Iter 70/100: 1.1575352477285392
Iter 80/100: 1.1516560261589057
Iter 90/100: 1.149788939285714
Iter 100/100: 1.1492764798741835
BO iteration:  72
Iter 10/100: 2.0555467927967492
Iter 20/100: 1.7469284501450786
Iter 30/100: 1.5123206574507606
Iter 40/100: 1.3741294140504736
Iter 50/100: 1.2845949427757175
Iter 60/100: 1.170067683365683
Iter 70/100: 1.1564016193737587
Iter 80/100: 1.1495764667896284
Iter 90/100: 1.1477818206718042
Iter 100/100: 1.1472716805266012
BO iteration:  73
Iter 10/100: 2.047035660792797
Iter 20/100: 1.740568272998283
Iter 30/100: 1.5060025768267853
Iter 40/100: 1.3647528447339499
Iter 50/100: 1.2708299956699614
Iter 60/100: 1.172490637387826
Iter 70/100: 1.1543391958999392
Iter 80/100: 1.1469323671829768
Iter 90/100: 1.143611

Iter 50/100: 1.1284411044856841
Iter 60/100: 1.063527501511591
Iter 70/100: 1.0555415437741948
Iter 80/100: 1.0517642109543996
Iter 90/100: 1.0504328749621712
Iter 100/100: 1.0498217505146963
BO iteration:  96
Iter 10/100: 1.8827594585504184
Iter 20/100: 1.6139499907358266
Iter 30/100: 1.373903873381084
Iter 40/100: 1.2020458173365425
Iter 50/100: 1.1256350688419283
Iter 60/100: 1.061588138406571
Iter 70/100: 1.0536603736477652
Iter 80/100: 1.049987325307371
Iter 90/100: 1.0486304318367479
Iter 100/100: 1.0480231080008389
BO iteration:  97
Iter 10/100: 1.8771312831635867
Iter 20/100: 1.6096181253198534
Iter 30/100: 1.3693403692430262
Iter 40/100: 1.1960461542723124
Iter 50/100: 1.1203219932140807
Iter 60/100: 1.0594378308584222
Iter 70/100: 1.0509934648090973
Iter 80/100: 1.0472086219959589
Iter 90/100: 1.0458452608981916
Iter 100/100: 1.0452442366230557
BO iteration:  98
Iter 10/100: 1.8712002145702653
Iter 20/100: 1.6046114994908955
Iter 30/100: 1.363757845415633
Iter 40/100: 1.18998

Iter 40/100: 1.096543606672734
Iter 50/100: 1.014278195429952
Iter 60/100: 0.97018895007593
Iter 70/100: 0.9650139881164461
Iter 80/100: 0.962316507206376
Iter 90/100: 0.9612433220439226
Iter 100/100: 0.9607138013561318
BO iteration:  122
Iter 10/100: 1.7719246128972361
Iter 20/100: 1.52881212940756
Iter 30/100: 1.2902941328287731
Iter 40/100: 1.1041293839373119
Iter 50/100: 1.0231168145724867
BO iteration:  123
Iter 10/100: 1.7672999785323327
Iter 20/100: 1.5242771363471517
Iter 30/100: 1.2840068893533798
Iter 40/100: 1.0949165950706596
Iter 50/100: 1.0145062749112035
Iter 60/100: 0.9971199408421599
Iter 70/100: 0.9877304541936145
Iter 80/100: 0.9820000180997336
Iter 90/100: 0.9798020851408658
Iter 100/100: 0.9789092478775946
BO iteration:  124
Iter 10/100: 1.7636150704391624
Iter 20/100: 1.5213298765354772
Iter 30/100: 1.280687376443974
Iter 40/100: 1.0897919245755265
Iter 50/100: 1.009632482076998
Iter 60/100: 0.9945001708412966
Iter 70/100: 0.9845905154372508
Iter 80/100: 0.9786889

BO iteration:  148
Iter 10/100: 1.695642878789283
Iter 20/100: 1.4688670806297086
Iter 30/100: 1.2287730737156903
Iter 40/100: 1.0314535209327087
Iter 50/100: 0.9806361721354268
Iter 60/100: 0.9551146278568707
Iter 70/100: 0.9506680426193178
Iter 80/100: 0.9427923219965938
Iter 90/100: 0.9402120299581721
Iter 100/100: 0.9389089641232897
BO iteration:  149
Iter 10/100: 1.69502238108389
Iter 20/100: 1.4699523198267757
Iter 30/100: 1.233825686908063
Iter 40/100: 1.0436332313597658
Iter 50/100: 0.9936361647465205
Iter 60/100: 0.9727267448852228
Iter 70/100: 0.9673676844427771
Iter 80/100: 0.9631972826511169
Iter 90/100: 0.9619656809972053
Iter 100/100: 0.9616878167727659
elapsed_time:	 1.627364945411682  min.
total number of unique COFs acquired 139
woo, top COF acquired!
iteration we acquire top COF =  33
accumulated cost up to observation of top COF =  8598.018785762788  [min]
